# **Let's Try DDNM!**

Zero Shot Image Restoration Using Denoising Diffusion Null-Space Model

[Yinhuai Wang](https://wyhuai.github.io/info/)\*, Jiwen Yu\*, Jian Zhang

[Paper](https://arxiv.org/pdf/2212.00490.pdf) | [Project](https://wyhuai.github.io/ddnm.io/) | [Github](https://github.com/wyhuai/DDNM)

If you find this work useful, please consider citing:


```
@article{wang2022ddnm,
title={Zero Shot Image Restoration Using Denoising Diffusion Null-Space Model},
author={Yinhuai, Wang and Jiwen, Yu and Jian, Zhang},
journal={arXiv:2212.00490},
year={2022}}
}
```



# PREPARATION

In [4]:
pip install numpy torch blobfile tqdm pyYaml pillow

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
     |████████████████████████████████| 73 kB 4.2 MB/s eta 0:00:011
     |████████████████████████████████| 2.1 MB 7.6 MB/s eta 0:00:01
     |████████████████████████████████| 7.1 MB 34.0 MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [16]:
import torch

In [23]:
torch.cuda.empty_cache()

In [25]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '6'

In [1]:
!nvidia-smi

Tue May 16 11:48:09 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 450.156.00   Driver Version: 450.156.00   CUDA Version: 11.5     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  A100-SXM4-40GB      On   | 00000000:07:00.0 Off |                    0 |
| N/A   48C    P0   217W / 400W |  13890MiB / 40537MiB |     59%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
|   1  A100-SXM4-40GB      On   | 00000000:0F:00.0 Off |                    0 |
| N/A   

In [8]:
from psutil import virtual_memory
ram_gb = virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb))

if ram_gb < 20:
  print('Not using a high-RAM runtime')
else:
  print('You are using a high-RAM runtime!')

Your runtime has 1082.0 gigabytes of available RAM

You are using a high-RAM runtime!


# Download the pretrained models

In [7]:
cd hq_demo/data/pretrained

/workspace/DDNM/hq_demo/data/pretrained


In [8]:
!wget https://openaipublic.blob.core.windows.net/diffusion/jul-2021/256x256_classifier.pt # Trained by OpenAI

--2023-03-07 08:04:55--  https://openaipublic.blob.core.windows.net/diffusion/jul-2021/256x256_classifier.pt
Resolving openaipublic.blob.core.windows.net (openaipublic.blob.core.windows.net)... 20.150.77.132
Connecting to openaipublic.blob.core.windows.net (openaipublic.blob.core.windows.net)|20.150.77.132|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 216496432 (206M) [application/octet-stream]
Saving to: ‘256x256_classifier.pt.1’

256x256_classifier. 100%[===================>] 206.47M  1.29MB/s    in 2m 36s  

2023-03-07 08:07:31 (1.33 MB/s) - ‘256x256_classifier.pt.1’ saved [216496432/216496432]



In [2]:
!wget https://openaipublic.blob.core.windows.net/diffusion/jul-2021/256x256_diffusion.pt # Trained by OpenAI

--2023-03-07 09:05:22--  https://openaipublic.blob.core.windows.net/diffusion/jul-2021/256x256_diffusion.pt
Resolving openaipublic.blob.core.windows.net (openaipublic.blob.core.windows.net)... 20.150.77.132
Connecting to openaipublic.blob.core.windows.net (openaipublic.blob.core.windows.net)|20.150.77.132|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2215479544 (2.1G) [application/octet-stream]
Saving to: ‘256x256_diffusion.pt’

256x256_diffusion.p  57%[==========>         ]   1.19G   994KB/s    eta 13m 3s ^C


Environment setup

# **DDNM for Raindrop Removal**
This is under research

In [29]:
%pwd

'/workspace/DDNM'

In [30]:
cd /workspace/DDNM/

/workspace/DDNM


## Force other degradation method
Because there is no SVD operator, degradation matrix, etc for raindrop removal, we use some similar degradation, such as denoising, deblruing, and inpainting

### simplified_imagenet_raindrop_denoising

In [13]:
cd /workspace/DDNM

/workspace/DDNM


In [14]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
    

    temp = "FIX_SIMP_WITHOUT_MASK"
    !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "denoising" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

Processing image: 0_rain.png
INFO - main.py - 2023-05-29 08:52:01,178 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 36.41: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.43s/it]
[tensor(36.4078, device='cuda:0')]
Total Average PSNR: 36.41
Number of samples: 1
Processing image: 10_rain.png
INFO - main.py - 2023-05-29 08:52:39,052 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig

PSNR: 35.20: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.58s/it]
[tensor(35.1964, device='cuda:0')]
Total Average PSNR: 35.20
Number of samples: 1
Processing image: 13_rain.png
INFO - main.py - 2023-05-29 08:54:19,518 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 38.30: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.36s/it]
[tensor(38.3042, device='cuda:0')]
Total Average PSNR: 38.30
Number of samples: 1
Processing image: 14_rain.png
INFO - main.py - 2023-05-29 08:54:53,946 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_

PSNR: 35.60: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.95s/it]
[tensor(35.5997, device='cuda:0')]
Total Average PSNR: 35.60
Number of samples: 1
Processing image: 16_rain.png
INFO - main.py - 2023-05-29 08:56:03,917 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.75: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.37s/it]
[tensor(35.7490, device='cuda:0')]
Total Average PSNR: 35.75
Number of samples: 1
Processing image: 17_rain.png
INFO - main.py - 2023-05-29 08:56:42,184 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_

PSNR: 36.17: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.97s/it]
[tensor(36.1732, device='cuda:0')]
Total Average PSNR: 36.17
Number of samples: 1
Processing image: 19_rain.png
INFO - main.py - 2023-05-29 08:57:52,316 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 33.54: 100%|████████████████████████████████| 1/1 [00:20<00:00, 21.00s/it]
[tensor(33.5410, device='cuda:0')]
Total Average PSNR: 33.54
Number of samples: 1
Processing image: 1_rain.png
INFO - main.py - 2023-05-29 08:58:30,221 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_v

PSNR: 33.03: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.88s/it]
[tensor(33.0282, device='cuda:0')]
Total Average PSNR: 33.03
Number of samples: 1
Processing image: 21_rain.png
INFO - main.py - 2023-05-29 08:59:39,593 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.19: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.17s/it]
[tensor(35.1894, device='cuda:0')]
Total Average PSNR: 35.19
Number of samples: 1
Processing image: 22_rain.png
INFO - main.py - 2023-05-29 09:00:13,752 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_

...

Processing image: 53_rain.png
INFO - main.py - 2023-05-29 09:18:22,130 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  0%|                                                     | 0/1 [00:05<?, ?it/s]
ERROR - main.py - 2023-05-29 09:18:37,745 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 535, in simplified_ddnm_plus
    et = model(xt, t)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1110, in _call_im

Processing image: 55_rain.png
INFO - main.py - 2023-05-29 09:18:58,470 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  0%|                                                     | 0/1 [00:05<?, ?it/s]
ERROR - main.py - 2023-05-29 09:19:14,130 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 535, in simplified_ddnm_plus
    et = model(xt, t)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1110, in _call_im

Processing image: 57_rain.png
INFO - main.py - 2023-05-29 09:19:37,320 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  0%|                                                     | 0/1 [00:04<?, ?it/s]
ERROR - main.py - 2023-05-29 09:19:52,471 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 535, in simplified_ddnm_plus
    et = model(xt, t)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1110, in _call_im

Processing image: 6_rain.png
INFO - main.py - 2023-05-29 09:20:16,803 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  0%|                                                     | 0/1 [00:04<?, ?it/s]
ERROR - main.py - 2023-05-29 09:20:31,821 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 535, in simplified_ddnm_plus
    et = model(xt, t)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1110, in _call_imp

Processing image: 8_rain.png
INFO - main.py - 2023-05-29 09:20:56,564 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  0%|                                                     | 0/1 [00:07<?, ?it/s]
ERROR - main.py - 2023-05-29 09:21:17,321 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 535, in simplified_ddnm_plus
    et = model(xt, t)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1110, in _call_imp

In [19]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] in ['51_rain.png', '52_rain.png', '53_rain.png', '54_rain.png', '55_rain.png', '56_rain.png', '57_rain.png', '5_rain.png', '6_rain.png', '7_rain.png', '8_rain.png', '9_rain.png']):
        print ('Processing image: %s'%(input_list[i]))
        #imagenet txt
        file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

        # Step 2: Open the file in write mode and truncate its content
        with open(file_path, 'w') as file:
            file.truncate(0)

            # Step 3: Write to the file
            file.write(input_list[i])
            file.write(' 0')


        temp = "FIX_SIMP_WITHOUT_MASK"
        !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "denoising" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

Processing image: 51_rain.png
INFO - main.py - 2023-05-29 09:31:24,784 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 34.14: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.11s/it]
[tensor(34.1366, device='cuda:0')]
Total Average PSNR: 34.14
Number of samples: 1
Processing image: 52_rain.png
INFO - main.py - 2023-05-29 09:32:03,834 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_ori

PSNR: 34.02: 100%|████████████████████████████████| 1/1 [00:20<00:00, 20.26s/it]
[tensor(34.0233, device='cuda:0')]
Total Average PSNR: 34.02
Number of samples: 1
Processing image: 54_rain.png
INFO - main.py - 2023-05-29 09:33:13,073 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 34.66: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.00s/it]
[tensor(34.6635, device='cuda:0')]
Total Average PSNR: 34.66
Number of samples: 1
Processing image: 55_rain.png
INFO - main.py - 2023-05-29 09:33:48,477 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_

Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 34.39: 100%|████████████████████████████████| 1/1 [00:20<00:00, 20.50s/it]
[tensor(34.3937, device='cuda:0')]
Total Average PSNR: 34.39
Number of samples: 1
Processing image: 57_rain.png
INFO - main.py - 2023-05-29 09:34:55,203 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.95: 100%|████████████████████████████████| 1

PSNR: 34.61: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.39s/it]
[tensor(34.6066, device='cuda:0')]
Total Average PSNR: 34.61
Number of samples: 1
Processing image: 7_rain.png
INFO - main.py - 2023-05-29 09:36:24,266 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: denoising
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.28: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.19s/it]
[tensor(35.2768, device='cuda:0')]
Total Average PSNR: 35.28
Number of samples: 1
Processing image: 8_rain.png
INFO - main.py - 2023-05-29 09:36:51,064 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_va

PSNR: 34.31: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.15s/it]
[tensor(34.3100, device='cuda:0')]
Total Average PSNR: 34.31
Number of samples: 1


In [21]:
import os
import shutil

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_SIMP_WITHOUT_MASK" + input_list[i].split(".")[0] + "/-1_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/RES_SIMP_WITHOUT_MASK/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [11]:
cd /workspace/DDNM/exp/datasets/imagenet/imagenet/

/workspace/DDNM/exp/datasets/imagenet/imagenet


In [12]:
rm -r .ipynb_checkpoints

### imagenet_raindrop_denoising

In [26]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
    

    temp = "FIX_SVD_WITHOUT_MASK"
    !python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "denoising" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

Processing image: 0_rain.png
INFO - main.py - 2023-05-29 09:43:00,377 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 35.69: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.40s/it]
[tensor(35.6884, device='cuda:0')]
Total Average PSNR: 35.69
Number of samples: 1
Processing image: 10_rain.png
INFO - main.py - 2023-05-29 09:43:29,047 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 39.90: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.39s/it]
[tensor(39.9049, device='cuda:0')]
Total Average PSNR: 39.90
Number of samples: 1
Processing image: 11_rain.png
INFO - main.py - 2023-05-29 09:43:57,045 - Using device: cuda
Run SVD-based DDNM. 100

PSNR: 33.35: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.63s/it]
[tensor(33.3509, device='cuda:0')]
Total Average PSNR: 33.35
Number of samples: 1
Processing image: 13_rain.png
INFO - main.py - 2023-05-29 09:44:52,972 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 37.41: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.16s/it]
[tensor(37.4146, device='cuda:0')]
Total Average PSNR: 37.41
Number of samples: 1
Processing image: 14_rain.png
INFO - main.py - 2023-05-29 09:45:23,994 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.05: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.49s/it]
[tensor(33.0548, device='cuda:0')

PSNR: 34.14: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.40s/it]
[tensor(34.1409, device='cuda:0')]
Total Average PSNR: 34.14
Number of samples: 1
Processing image: 16_rain.png
INFO - main.py - 2023-05-29 09:46:20,510 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 34.78: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.59s/it]
[tensor(34.7775, device='cuda:0')]
Total Average PSNR: 34.78
Number of samples: 1
Processing image: 17_rain.png
INFO - main.py - 2023-05-29 09:46:47,103 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 36.37: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.21s/it]
[tensor(36.3654, device='cuda:0')

PSNR: 31.99: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.58s/it]
[tensor(31.9931, device='cuda:0')]
Total Average PSNR: 31.99
Number of samples: 1
Processing image: 1_rain.png
INFO - main.py - 2023-05-29 09:48:18,255 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.52: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.75s/it]
[tensor(33.5175, device='cuda:0')]
Total Average PSNR: 33.52
Number of samples: 1
Processing image: 20_rain.png
INFO - main.py - 2023-05-29 09:48:48,021 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 32.40: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.03s/it]
[tensor(32.3968, device='cuda:0')]

PSNR: 34.01: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.26s/it]
[tensor(34.0128, device='cuda:0')]
Total Average PSNR: 34.01
Number of samples: 1
Processing image: 22_rain.png
INFO - main.py - 2023-05-29 09:49:44,189 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.53: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.18s/it]
[tensor(33.5252, device='cuda:0')]
Total Average PSNR: 33.53
Number of samples: 1
Processing image: 23_rain.png
INFO - main.py - 2023-05-29 09:50:13,787 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.32: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.57s/it]
[tensor(33.3246, device='cuda:0')

...

PSNR: 35.17: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.12s/it]
[tensor(35.1716, device='cuda:0')]
Total Average PSNR: 35.17
Number of samples: 1
Processing image: 50_rain.png
INFO - main.py - 2023-05-29 10:04:44,510 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 34.41: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.49s/it]
[tensor(34.4146, device='cuda:0')]
Total Average PSNR: 34.41
Number of samples: 1
Processing image: 51_rain.png
INFO - main.py - 2023-05-29 10:05:13,544 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 32.97: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.42s/it]
[tensor(32.9729, device='cuda:0')

PSNR: 30.93: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.03s/it]
[tensor(30.9295, device='cuda:0')]
Total Average PSNR: 30.93
Number of samples: 1
Processing image: 53_rain.png
INFO - main.py - 2023-05-29 10:06:17,710 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 32.58: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.93s/it]
[tensor(32.5810, device='cuda:0')]
Total Average PSNR: 32.58
Number of samples: 1
Processing image: 54_rain.png
INFO - main.py - 2023-05-29 10:06:49,459 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.07: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.41s/it]
[tensor(33.0716, device='cuda:0')

PSNR: 32.88: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.38s/it]
[tensor(32.8793, device='cuda:0')]
Total Average PSNR: 32.88
Number of samples: 1
Processing image: 57_rain.png
INFO - main.py - 2023-05-29 10:08:11,549 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 35.18: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.13s/it]
[tensor(35.1844, device='cuda:0')]
Total Average PSNR: 35.18
Number of samples: 1
Processing image: 5_rain.png
INFO - main.py - 2023-05-29 10:08:39,800 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 37.61: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.06s/it]
[tensor(37.6129, device='cuda:0')]

PSNR: 34.04: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.22s/it]
[tensor(34.0408, device='cuda:0')]
Total Average PSNR: 34.04
Number of samples: 1
Processing image: 7_rain.png
INFO - main.py - 2023-05-29 10:09:41,111 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 34.19: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.60s/it]
[tensor(34.1911, device='cuda:0')]
Total Average PSNR: 34.19
Number of samples: 1
Processing image: 8_rain.png
INFO - main.py - 2023-05-29 10:10:08,295 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 34.80: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.06s/it]
[tensor(34.7950, device='cuda:0')]


PSNR: 32.26: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.02s/it]
[tensor(32.2599, device='cuda:0')]
Total Average PSNR: 32.26
Number of samples: 1


In [28]:
import os
import shutil

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_SVD_WITHOUT_MASK" + input_list[i].split(".")[0] + "/0_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/RES_SVD_WITHOUT_MASK/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [19]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "denoising" --sigma_y 0.1 -i res_svd

INFO - main.py - 2023-04-03 09:25:22,184 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: denoising.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 6
Start from 0
 87%|████████████████████████████████████▌     | 87/100 [00:12<00:01,  6.88it/s]


 77%|████████████████████████████████▎         | 77/100 [00:11<00:03,  6.91it/s]


 67%|████████████████████████████▏             | 67/100 [00:09<00:04,  6.94it/s]


PSNR: 34.60: 100%|████████████████████████████████| 6/6 [01:37<00:00, 16.23s/it]
[tensor(39.9036, device='cuda:0'), tensor(38.3427, device='cuda:0'), tensor(36.4430, device='cuda:0'), tensor(35.2140, device='cuda:0'), tensor(34.9079, device='cuda:0'), tensor(34.6000, device='cuda:0')]
Total Average PSNR: 36.57
Number of samples: 6
CPU times: user 927 ms, sys: 409 ms, total: 1.34 s
Wall time: 1min 50s


In [10]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "deblur_uni" --sigma_y 0.1 -i res_svd_deblur_uni

INFO - main.py - 2023-04-04 06:16:06,066 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: deblur_uni.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 6
Start from 0
 64%|██████████████████████████▉               | 64/100 [00:04<00:02, 13.50it/s]


PSNR: 28.85: 100%|████████████████████████████████| 6/6 [00:53<00:00,  8.93s/it]
[tensor(31.9229, device='cuda:0'), tensor(32.3018, device='cuda:0'), tensor(30.8418, device='cuda:0'), tensor(29.7670, device='cuda:0'), tensor(29.2412, device='cuda:0'), tensor(28.8513, device='cuda:0')]
Total Average PSNR: 30.49
Number of samples: 6
CPU times: user 569 ms, sys: 327 ms, total: 895 ms
Wall time: 1min 5s


### deblur_gauss

In [14]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "deblur_gauss" --sigma_y 0.1 -i res_svd_deblur_gauss

INFO - main.py - 2023-04-04 06:19:12,608 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: deblur_gauss.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 6
Start from 0
 64%|██████████████████████████▉               | 64/100 [00:04<00:02, 13.54it/s]


PSNR: 30.95: 100%|████████████████████████████████| 6/6 [00:53<00:00,  8.88s/it]
[tensor(35.2515, device='cuda:0'), tensor(34.6993, device='cuda:0'), tensor(32.9864, device='cuda:0'), tensor(31.8504, device='cuda:0'), tensor(31.2892, device='cuda:0'), tensor(30.9485, device='cuda:0')]
Total Average PSNR: 32.84
Number of samples: 6
CPU times: user 595 ms, sys: 433 ms, total: 1.03 s
Wall time: 1min 8s


## Raindrop Mask

### Threshold 0.5

### simplified 

In [2]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_0

INFO - main.py - 2023-04-04 17:05:57,571 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 34.26: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.43s/it]
[tensor(34.2621, device='cuda:0')]
Total Average PSNR: 34.26
Number of samples: 1


In [3]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_1

INFO - main.py - 2023-04-04 17:07:30,652 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 26.15: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.92s/it]
[tensor(26.1527, device='cuda:0')]
Total Average PSNR: 26.15
Number of samples: 1


In [4]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_2

INFO - main.py - 2023-04-04 17:08:37,605 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 27.75: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.35s/it]
[tensor(27.7524, device='cuda:0')]
Total Average PSNR: 27.75
Number of samples: 1


In [18]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_3

INFO - main.py - 2023-04-05 09:15:21,623 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 24.56: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.97s/it]
[tensor(24.5553, device='cuda:0')]
Total Average PSNR: 24.56
Number of samples: 1


In [19]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_4

INFO - main.py - 2023-04-05 09:16:20,663 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 27.08: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.29s/it]
[tensor(27.0807, device='cuda:0')]
Total Average PSNR: 27.08
Number of samples: 1


In [7]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_5

INFO - main.py - 2023-04-04 17:11:38,441 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 27.48: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.86s/it]
[tensor(27.4831, device='cuda:0')]
Total Average PSNR: 27.48
Number of samples: 1


In [8]:
%pwd

'/workspace/DDNM'

In [22]:
cd /workspace/DDNM

/workspace/DDNM


In [9]:
!python calculate_psnr_ssim.py

Traceback (most recent call last):
  File "calculate_psnr_ssim.py", line 3, in <module>
    from utils.metrics import calculate_psnr, calculate_ssim
ModuleNotFoundError: No module named 'utils'


In [78]:
cd /workspace/DDNM/exp/datasets/imagenet/gt_256

/workspace/DDNM/exp/datasets/imagenet/gt_256


In [28]:
cd /workspace/DDNM/exp/image_samples/res_dam_rmd_in_rd_rdm

/workspace/DDNM/exp/image_samples/res_dam_rmd_in_rd_rdm


In [29]:
rm -r .ipynb_checkpoints

### Conditional

In [34]:
!python main.py --ni --simplified --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i cond_s_in_rd_rdm_0

INFO - main.py - 2023-04-23 14:41:28,947 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
  0%|                                                     | 0/1 [00:02<?, ?it/s]
ERROR - main.py - 2023-04-23 14:41:40,936 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 479, in simplified_ddnm_plus
    et = model(xt, t)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1110, in _call_impl
    return forward_call(*input, **kwargs)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/parallel/data_parallel.py", line 166, in for

INFO - main.py - 2023-04-23 15:46:58,051 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
  0%|                                                     | 0/1 [00:02<?, ?it/s]
ERROR - main.py - 2023-04-23 15:47:12,158 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 425, in simplified_ddnm_plus
    y = A(x_orig)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 364, in <lambda>
    A = lambda z: A_mask(A_blur(z))
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 353, in <lambda>
    A_mask = lambda z: z*mask
RuntimeError: The size of

### Not simplified

ilang

### conditional

In [2]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_0

INFO - main.py - 2023-04-22 13:02:02,166 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 31.80: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.56s/it]
[tensor(31.8032, device='cuda:0')]
Total Average PSNR: 31.80
Number of samples: 1
CPU times: user 392 ms, sys: 176 ms, total: 567 ms
Wall time: 47.9 s


In [3]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_1

INFO - main.py - 2023-04-22 13:06:30,853 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 25.30: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.70s/it]
[tensor(25.3042, device='cuda:0')]
Total Average PSNR: 25.30
Number of samples: 1
CPU times: user 333 ms, sys: 216 ms, total: 548 ms
Wall time: 45.5 s


In [4]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_2

INFO - main.py - 2023-04-22 13:07:39,991 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 27.75: 100%|████████████████████████████████| 1/1 [00:25<00:00, 25.35s/it]
[tensor(27.7529, device='cuda:0')]
Total Average PSNR: 27.75
Number of samples: 1
CPU times: user 366 ms, sys: 246 ms, total: 612 ms
Wall time: 46.3 s


In [5]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_3

INFO - main.py - 2023-04-22 13:09:54,861 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 24.57: 100%|████████████████████████████████| 1/1 [00:26<00:00, 26.09s/it]
[tensor(24.5699, device='cuda:0')]
Total Average PSNR: 24.57
Number of samples: 1
CPU times: user 318 ms, sys: 298 ms, total: 616 ms
Wall time: 47.2 s


In [6]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_4

INFO - main.py - 2023-04-22 13:11:15,993 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 26.62: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.18s/it]
[tensor(26.6171, device='cuda:0')]
Total Average PSNR: 26.62
Number of samples: 1
CPU times: user 374 ms, sys: 175 ms, total: 549 ms
Wall time: 49.7 s


In [7]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_5

INFO - main.py - 2023-04-22 13:13:20,888 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 27.25: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.51s/it]
[tensor(27.2485, device='cuda:0')]
Total Average PSNR: 27.25
Number of samples: 1
CPU times: user 331 ms, sys: 140 ms, total: 471 ms
Wall time: 43.7 s


## Deblur gauss with mask

In [86]:
import gc
import torch
def report_gpu():
   print(torch.cuda.list_gpu_processes())
   gc.collect()
   torch.cuda.empty_cache()

In [87]:
import gc
gc.collect()
torch.cuda.empty_cache()

In [48]:
cd /workspace/DDNM/

/workspace/DDNM


In [90]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "deblur_gauss" --sigma_y 0.1 -i dg_in_rd_rdm_0_tt

INFO - main.py - 2023-04-21 17:58:58,870 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: deblur_gauss.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
deblur_gauss
yeay
init_awal
init_akhir
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak

  0%|                                                  | 0/1210 [00:00<?, ?it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

  0%|                                        | 1/1210 [00:04<1:38:19,  4.88s/it]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw


Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

  6%|██▍                                      | 71/1210 [00:07<00:42, 26.62it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

  8%|███                                      | 91/1210 [00:07<00:20, 53.86it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut a

Lam ak
LN aw
Ln ak

 21%|████████▌                               | 258/1210 [00:14<00:27, 34.35it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 22%|████████▋                               | 263/1210 [00:14<00:33, 28.18it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut a

Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 30%|███████████▊                            | 358/1210 [00:18<00:26, 32.36it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec


Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 35%|██████████████▏                         | 429/1210 [00:21<00:44, 17.73it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 37%|██████████████▉                         | 451/1210 [00:21<00:13, 55.76it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut a

Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 43%|█████████████████▎                      | 525/1210 [00:24<00:36, 18.53it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 44%|█████████████████▍                      | 527/1210 [00:24<00:37, 18.07it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 44%|█████████████████▍                      | 529/1210 [00:24<00:38, 17.73it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak


Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 59%|███████████████████████▋                | 716/1210 [00:31<00:23, 21.27it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 59%|███████████████████████▊                | 719/1210 [00:31<00:24, 20.15it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhi

Ln ak

 75%|█████████████████████████████▉          | 904/1210 [00:37<00:10, 28.43it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 75%|██████████████████████████████          | 909/1210 [00:38<00:12, 24.75it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pin

Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 91%|███████████████████████████████████▍   | 1098/1210 [00:44<00:03, 35.02it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec


Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 97%|█████████████████████████████████████▋ | 1171/1210 [00:48<00:01, 26.11it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak

 98%|██████████████████████████████████████▍| 1191/1210 [00:48<00:00, 52.08it/s]Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhir
add_zeros exec
V_aw
V_ak
L aw
Lam ak
LN aw
Ln ak
Vt awal
Vt akh
singulars exec
U aw
U akh
A_pinv awal
Ut aw
Ut ak
A_pinv akhi

In [86]:
CUDA_LAUNCH_BLOCKING = 1

In [87]:
!export PYTORCH_CUDA_ALLOC_CONF=garbage_collection_threshold:0.6,max_split_size_mb:128

In [66]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i rmd_s_in_rd_rdm_0

INFO - main.py - 2023-04-23 16:54:45,056 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
  0%|                                                     | 0/1 [00:01<?, ?it/s]
ERROR - main.py - 2023-04-23 16:54:56,773 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 444, in simplified_ddnm_plus
    tvu.save_image(
  File "/opt/conda/lib/python3.8/site-packages/torch/autograd/grad_mode.py", line 28, in decorate_context
    return func(*args, **kwargs)
  File "/opt/conda/lib/python3.8/site-packages/torchvision/utils.py", line 132, in save_image
    grid = m

In [54]:
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "deblur_gauss_old" --sigma_y 0.1 -i rmd_s_in_rd_rdm_0

INFO - main.py - 2023-04-23 16:27:23,999 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: deblur_gauss_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
  0%|                                                     | 0/1 [00:33<?, ?it/s]
Traceback (most recent call last):
  File "main.py", line 174, in <module>
    sys.exit(main())
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 292, in sample
    self.svd_based_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 757, in svd_based_ddnm_plus
    tvu.save_image(
  File "/workspace/DDNM/functions/svd_ddnm.py", line 108, in ddnm_plus_diffusion
    et = model(xt, t)
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1110, in _call_impl
    return forward_call(*input, **kwargs)
  File "/opt/conda/

### Deblur gauss with mask

In [67]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i dgm_rmd_in_rd_rdm_0

INFO - main.py - 2023-04-27 16:38:07,654 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 34.03: 100%|████████████████████████████████| 1/1 [00:21<00:00, 21.82s/it]
[tensor(34.0298, device='cuda:0')]
Total Average PSNR: 34.03
Number of samples: 1


In [68]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i dgm_rmd_in_rd_rdm_1

INFO - main.py - 2023-04-27 16:39:44,464 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.10: 100%|████████████████████████████████| 1/1 [00:22<00:00, 22.12s/it]
[tensor(26.1031, device='cuda:0')]
Total Average PSNR: 26.10
Number of samples: 1


In [69]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i dgm_rmd_in_rd_rdm_2

INFO - main.py - 2023-04-27 16:42:28,459 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.61: 100%|████████████████████████████████| 1/1 [00:22<00:00, 22.88s/it]
[tensor(27.6053, device='cuda:0')]
Total Average PSNR: 27.61
Number of samples: 1


In [76]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i dgm_rmd_in_rd_rdm_3

INFO - main.py - 2023-04-27 17:02:53,311 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.51: 100%|████████████████████████████████| 1/1 [00:22<00:00, 22.35s/it]
[tensor(24.5130, device='cuda:0')]
Total Average PSNR: 24.51
Number of samples: 1


In [77]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i dgm_rmd_in_rd_rdm_4

INFO - main.py - 2023-04-27 17:04:24,668 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.99: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.15s/it]
[tensor(26.9869, device='cuda:0')]
Total Average PSNR: 26.99
Number of samples: 1


In [72]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i dgm_rmd_in_rd_rdm_5

INFO - main.py - 2023-04-27 16:50:56,357 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.40: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.04s/it]
[tensor(27.3976, device='cuda:0')]
Total Average PSNR: 27.40
Number of samples: 1


In [105]:
cd /workspace/DDNM/

/workspace/DDNM


### Deblur Uni with mask

In [3]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i dum_rmd_in_rd_rdm_0

INFO - main.py - 2023-05-03 11:11:17,209 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 33.93: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.21s/it]
[tensor(33.9332, device='cuda:0')]
Total Average PSNR: 33.93
Number of samples: 1


In [14]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i dum_rmd_in_rd_rdm_1

INFO - main.py - 2023-05-03 13:42:28,815 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.03: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.98s/it]
[tensor(26.0274, device='cuda:0')]
Total Average PSNR: 26.03
Number of samples: 1


In [15]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i dum_rmd_in_rd_rdm_2

INFO - main.py - 2023-05-03 13:43:29,559 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.46: 100%|████████████████████████████████| 1/1 [00:26<00:00, 26.35s/it]
[tensor(27.4631, device='cuda:0')]
Total Average PSNR: 27.46
Number of samples: 1


In [16]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i dum_rmd_in_rd_rdm_3

INFO - main.py - 2023-05-03 13:44:32,044 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.51: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.77s/it]
[tensor(24.5059, device='cuda:0')]
Total Average PSNR: 24.51
Number of samples: 1


In [17]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i dum_rmd_in_rd_rdm_4

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 3.58 µs
INFO - main.py - 2023-05-03 13:45:53,971 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.90: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.95s/it]
[tensor(26.9018, device='cuda:0')]
Total Average PSNR: 26.90
Number of samples: 1


In [18]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i dum_rmd_in_rd_rdm_5

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 4.05 µs
INFO - main.py - 2023-05-03 13:47:09,824 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.28: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.87s/it]
[tensor(27.2813, device='cuda:0')]
Total Average PSNR: 27.28
Number of samples: 1


### deblur aniso with mask

In [20]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i dam_rmd_in_rd_rdm_0

CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 4.53 µs
INFO - main.py - 2023-05-03 13:53:09,707 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 33.93: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.68s/it]
[tensor(33.9284, device='cuda:0')]
Total Average PSNR: 33.93
Number of samples: 1


In [21]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i dam_rmd_in_rd_rdm_1

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 3.34 µs
INFO - main.py - 2023-05-03 13:56:24,064 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.06: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.90s/it]
[tensor(26.0573, device='cuda:0')]
Total Average PSNR: 26.06
Number of samples: 1


In [22]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i dam_rmd_in_rd_rdm_2

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 2.86 µs
INFO - main.py - 2023-05-03 13:57:40,701 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.56: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.95s/it]
[tensor(27.5628, device='cuda:0')]
Total Average PSNR: 27.56
Number of samples: 1


In [23]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i dam_rmd_in_rd_rdm_3

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 3.1 µs
INFO - main.py - 2023-05-03 13:59:33,395 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.47: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.75s/it]
[tensor(24.4671, device='cuda:0')]
Total Average PSNR: 24.47
Number of samples: 1


In [24]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i dam_rmd_in_rd_rdm_4

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 3.81 µs
INFO - main.py - 2023-05-03 14:03:07,887 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.95: 100%|████████████████████████████████| 1/1 [00:26<00:00, 26.51s/it]
[tensor(26.9465, device='cuda:0')]
Total Average PSNR: 26.95
Number of samples: 1


In [33]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i dam_rmd_in_rd_rdm_5

CPU times: user 0 ns, sys: 1 µs, total: 1 µs
Wall time: 3.34 µs
INFO - main.py - 2023-05-03 15:54:44,850 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.31: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.51s/it]
[tensor(27.3134, device='cuda:0')]
Total Average PSNR: 27.31
Number of samples: 1


### Time Travel Deblur with Mask

### Deblur gauss with mask

In [35]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i tt_dgm_rmd_in_rd_rdm_0

INFO - main.py - 2023-05-03 16:50:19,700 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 38%|███████████████                         | 454/1210 [00:48<00:42, 17.85it/s]


 76%|██████████████████████████████▌         | 925/1210 [01:33<00:41,  6.91it/s]


PSNR: 36.11: 100%|███████████████████████████████| 1/1 [02:00<00:00, 120.60s/it]
[tensor(36.1138, device='cuda:0')]
Total Average PSNR: 36.11
Number of samples: 1


In [36]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i tt_dgm_rmd_in_rd_rdm_1

INFO - main.py - 2023-05-03 16:55:39,847 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 35%|██████████████▏                         | 428/1210 [00:47<01:53,  6.91it/s]


 77%|██████████████████████████████▋         | 928/1210 [01:33<00:40,  6.91it/s]


PSNR: 27.40: 100%|███████████████████████████████| 1/1 [02:00<00:00, 120.03s/it]
[tensor(27.3992, device='cuda:0')]
Total Average PSNR: 27.40
Number of samples: 1


In [37]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i tt_dgm_rmd_in_rd_rdm_2

INFO - main.py - 2023-05-03 16:58:50,176 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 35%|██████████████▏                         | 428/1210 [00:47<01:53,  6.89it/s]


 76%|██████████████████████████████▍         | 922/1210 [01:32<00:41,  6.88it/s]


PSNR: 28.61: 100%|███████████████████████████████| 1/1 [02:00<00:00, 120.67s/it]
[tensor(28.6067, device='cuda:0')]
Total Average PSNR: 28.61
Number of samples: 1


In [76]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i tt_dgm_rmd_in_rd_rdm_3

INFO - main.py - 2023-04-27 17:02:53,311 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.51: 100%|████████████████████████████████| 1/1 [00:22<00:00, 22.35s/it]
[tensor(24.5130, device='cuda:0')]
Total Average PSNR: 24.51
Number of samples: 1


In [77]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i tt_dgm_rmd_in_rd_rdm_4

INFO - main.py - 2023-04-27 17:04:24,668 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.99: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.15s/it]
[tensor(26.9869, device='cuda:0')]
Total Average PSNR: 26.99
Number of samples: 1


In [72]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i tt_dgm_rmd_in_rd_rdm_5

INFO - main.py - 2023-04-27 16:50:56,357 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.40: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.04s/it]
[tensor(27.3976, device='cuda:0')]
Total Average PSNR: 27.40
Number of samples: 1


In [105]:
cd /workspace/DDNM/

/workspace/DDNM


### Deblur Uni with mask

In [3]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i tt_dum_rmd_in_rd_rdm_0

INFO - main.py - 2023-05-03 11:11:17,209 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 33.93: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.21s/it]
[tensor(33.9332, device='cuda:0')]
Total Average PSNR: 33.93
Number of samples: 1


In [14]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i tt_dum_rmd_in_rd_rdm_1

INFO - main.py - 2023-05-03 13:42:28,815 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.03: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.98s/it]
[tensor(26.0274, device='cuda:0')]
Total Average PSNR: 26.03
Number of samples: 1


In [15]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i tt_dum_rmd_in_rd_rdm_2

INFO - main.py - 2023-05-03 13:43:29,559 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.46: 100%|████████████████████████████████| 1/1 [00:26<00:00, 26.35s/it]
[tensor(27.4631, device='cuda:0')]
Total Average PSNR: 27.46
Number of samples: 1


In [16]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i tt_dum_rmd_in_rd_rdm_3

INFO - main.py - 2023-05-03 13:44:32,044 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.51: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.77s/it]
[tensor(24.5059, device='cuda:0')]
Total Average PSNR: 24.51
Number of samples: 1


In [17]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i tt_dum_rmd_in_rd_rdm_4

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 3.58 µs
INFO - main.py - 2023-05-03 13:45:53,971 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.90: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.95s/it]
[tensor(26.9018, device='cuda:0')]
Total Average PSNR: 26.90
Number of samples: 1


In [18]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i tt_dum_rmd_in_rd_rdm_5

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 4.05 µs
INFO - main.py - 2023-05-03 13:47:09,824 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.28: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.87s/it]
[tensor(27.2813, device='cuda:0')]
Total Average PSNR: 27.28
Number of samples: 1


### deblur aniso with mask

In [20]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i tt_dam_rmd_in_rd_rdm_0

CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 4.53 µs
INFO - main.py - 2023-05-03 13:53:09,707 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 33.93: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.68s/it]
[tensor(33.9284, device='cuda:0')]
Total Average PSNR: 33.93
Number of samples: 1


In [21]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i tt_dam_rmd_in_rd_rdm_1

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 3.34 µs
INFO - main.py - 2023-05-03 13:56:24,064 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.06: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.90s/it]
[tensor(26.0573, device='cuda:0')]
Total Average PSNR: 26.06
Number of samples: 1


In [22]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i tt_dam_rmd_in_rd_rdm_2

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 2.86 µs
INFO - main.py - 2023-05-03 13:57:40,701 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.56: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.95s/it]
[tensor(27.5628, device='cuda:0')]
Total Average PSNR: 27.56
Number of samples: 1


In [23]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i tt_dam_rmd_in_rd_rdm_3

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 3.1 µs
INFO - main.py - 2023-05-03 13:59:33,395 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.47: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.75s/it]
[tensor(24.4671, device='cuda:0')]
Total Average PSNR: 24.47
Number of samples: 1


In [24]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i tt_dam_rmd_in_rd_rdm_4

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 3.81 µs
INFO - main.py - 2023-05-03 14:03:07,887 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.95: 100%|████████████████████████████████| 1/1 [00:26<00:00, 26.51s/it]
[tensor(26.9465, device='cuda:0')]
Total Average PSNR: 26.95
Number of samples: 1


In [33]:
%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i tt_dam_rmd_in_rd_rdm_5

CPU times: user 0 ns, sys: 1 µs, total: 1 µs
Wall time: 3.34 µs
INFO - main.py - 2023-05-03 15:54:44,850 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.31: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.51s/it]
[tensor(27.3134, device='cuda:0')]
Total Average PSNR: 27.31
Number of samples: 1


### Conditional deblur with mask

### dg

### du

### da

In [31]:
cd /workspace/DDNM

/workspace/DDNM


In [32]:
%time
!python main.py --ni --simplified --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i dam_rmd_in_rd_rdm_5

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 2.86 µs
INFO - main.py - 2023-05-03 15:54:17,578 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  0%|                                                     | 0/1 [00:02<?, ?it/s]
ERROR - main.py - 2023-05-03 15:54:34,403 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 535, in simplified_ddnm_plus
    et = model(xt, t)
  File "/opt/conda/li

### WeatherDiff

### Threshold 0.5

In [83]:
!python main.py --ni --simplified --config raindrop_simple.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_wd_rd_rdm_0

Traceback (most recent call last):
  File "main.py", line 13, in <module>
    from guided_diffusion.diffusion import Diffusion
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 18, in <module>
    from guided_diffusion.script_util import create_model, create_classifier, classifier_defaults, args_to_dict
  File "/workspace/DDNM/guided_diffusion/script_util.py", line 6, in <module>
    from .unet import SuperResModel, UNetModel, EncoderUNetModel
ImportError: cannot import name 'SuperResModel' from 'guided_diffusion.unet' (/workspace/DDNM/guided_diffusion/unet.py)


In [3]:
!python main.py --ni --simplified --config raindrop_simple.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_wd_rd_rdm_1

INFO - main.py - 2023-04-04 17:07:30,652 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 26.15: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.92s/it]
[tensor(26.1527, device='cuda:0')]
Total Average PSNR: 26.15
Number of samples: 1


In [10]:
!python main.py --ni --simplified --config raindrop_simple.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_wd_rd_rdm_2

INFO - main.py - 2023-04-27 12:54:30,071 - Using device: cuda
ERROR - main.py - 2023-04-27 12:54:34,165 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 164, in sample
    model.load_state_dict(torch.load(ckpt, map_location=self.device))
  File "/opt/conda/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1490, in load_state_dict
    raise RuntimeError('Error(s) in loading state_dict for {}:\n\t{}'.format(
RuntimeError: Error(s) in loading state_dict for Model:
	Missing key(s) in state_dict: "temb.dense.0.weight", "temb.dense.0.bias", "temb.dense.1.weight", "temb.dense.1.bias", "conv_in.weight", "conv_in.bias", "down.0.block.0.norm1.weight", "down.0.block.0.norm1.bias", "down.0.block.0.conv1.weight", "down.0.block.0.conv1.bias", "down.0.block.0.temb_proj.weight", "down.0.block.0.temb_proj.bias", "down.0.block.0.norm2.weight", "down.0.block.0.norm2.bias", "

In [11]:
!python main.py --ni --simplified --config raindrop_simple.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_wd_rd_rdm_3

INFO - main.py - 2023-04-06 15:42:43,764 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/raindrop_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 11.54: 100%|████████████████████████████████| 1/1 [00:32<00:00, 32.92s/it]
[tensor(11.5372, device='cuda:0')]
Total Average PSNR: 11.54
Number of samples: 1


In [19]:
!python main.py --ni --simplified --config raindrop_simple.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_wd_rd_rdm_4

INFO - main.py - 2023-04-05 09:16:20,663 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 27.08: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.29s/it]
[tensor(27.0807, device='cuda:0')]
Total Average PSNR: 27.08
Number of samples: 1


In [7]:
!python main.py --ni --simplified --config raindrop_simple.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_wd_rd_rdm_5

INFO - main.py - 2023-04-04 17:11:38,441 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
PSNR: 27.48: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.86s/it]
[tensor(27.4831, device='cuda:0')]
Total Average PSNR: 27.48
Number of samples: 1


## DDNM+ and Time Travel

In [26]:
cd /workspace/DDNM/

/workspace/DDNM


### Simplified

In [29]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_0_tt

INFO - main.py - 2023-04-07 22:22:35,387 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
 79%|███████████████████████████████▍        | 951/1210 [00:48<00:04, 52.10it/s]


PSNR: 36.33: 100%|████████████████████████████████| 1/1 [01:02<00:00, 62.08s/it]
[tensor(36.3261, device='cuda:0')]
Total Average PSNR: 36.33
Number of samples: 1


In [30]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_1_tt

INFO - main.py - 2023-04-07 22:25:26,928 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
 79%|███████████████████████████████▌        | 956/1210 [00:49<00:08, 31.52it/s]


PSNR: 27.51: 100%|████████████████████████████████| 1/1 [01:02<00:00, 62.20s/it]
[tensor(27.5121, device='cuda:0')]
Total Average PSNR: 27.51
Number of samples: 1


In [31]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_2_tt

INFO - main.py - 2023-04-07 22:28:53,201 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
 79%|███████████████████████████████▍        | 950/1210 [00:51<00:04, 52.09it/s]


PSNR: 28.84: 100%|████████████████████████████████| 1/1 [01:05<00:00, 65.27s/it]
[tensor(28.8404, device='cuda:0')]
Total Average PSNR: 28.84
Number of samples: 1


In [32]:
%%time
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_3_tt

INFO - main.py - 2023-04-07 22:31:27,631 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
 76%|██████████████████████████████▌         | 924/1210 [00:48<00:19, 14.55it/s]


PSNR: 24.47: 100%|████████████████████████████████| 1/1 [01:02<00:00, 62.29s/it]
[tensor(24.4734, device='cuda:0')]
Total Average PSNR: 24.47
Number of samples: 1
CPU times: user 582 ms, sys: 328 ms, total: 910 ms
Wall time: 1min 13s


In [33]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_4_tt

INFO - main.py - 2023-04-07 22:33:31,954 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
 79%|███████████████████████████████▋        | 957/1210 [00:49<00:08, 31.00it/s]


PSNR: 27.26: 100%|████████████████████████████████| 1/1 [01:03<00:00, 63.40s/it]
[tensor(27.2641, device='cuda:0')]
Total Average PSNR: 27.26
Number of samples: 1


In [34]:
!python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i s_in_rd_rdm_5_tt

INFO - main.py - 2023-04-07 22:35:45,484 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
Start from 0
 79%|███████████████████████████████▋        | 957/1210 [00:50<00:08, 30.85it/s]


PSNR: 27.59: 100%|████████████████████████████████| 1/1 [01:03<00:00, 63.89s/it]
[tensor(27.5936, device='cuda:0')]
Total Average PSNR: 27.59
Number of samples: 1


### Not simplified

In [39]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i in_rd_rdm_0_tt

INFO - main.py - 2023-04-07 22:42:37,921 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 76%|██████████████████████████████▌         | 925/1210 [00:48<00:19, 14.51it/s]


PSNR: 33.47: 100%|████████████████████████████████| 1/1 [01:03<00:00, 63.51s/it]
[tensor(33.4699, device='cuda:0')]
Total Average PSNR: 33.47
Number of samples: 1
CPU times: user 679 ms, sys: 381 ms, total: 1.06 s
Wall time: 1min 24s


In [40]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i in_rd_rdm_1_tt

INFO - main.py - 2023-04-07 22:45:30,623 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 76%|██████████████████████████████▌         | 924/1210 [00:49<00:19, 14.49it/s]


PSNR: 26.49: 100%|████████████████████████████████| 1/1 [01:04<00:00, 64.89s/it]
[tensor(26.4852, device='cuda:0')]
Total Average PSNR: 26.49
Number of samples: 1
CPU times: user 691 ms, sys: 414 ms, total: 1.11 s
Wall time: 1min 24s


In [41]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i in_rd_rdm_2_tt

INFO - main.py - 2023-04-07 22:47:36,218 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 76%|██████████████████████████████▌         | 924/1210 [00:48<00:19, 14.42it/s]


PSNR: 27.13: 100%|████████████████████████████████| 1/1 [01:03<00:00, 63.17s/it]
[tensor(27.1321, device='cuda:0')]
Total Average PSNR: 27.13
Number of samples: 1
CPU times: user 606 ms, sys: 416 ms, total: 1.02 s
Wall time: 1min 23s


In [42]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i in_rd_rdm_3_tt

INFO - main.py - 2023-04-07 22:49:22,182 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 77%|██████████████████████████████▌         | 926/1210 [00:48<00:19, 14.21it/s]


PSNR: 24.02: 100%|████████████████████████████████| 1/1 [01:03<00:00, 63.28s/it]
[tensor(24.0163, device='cuda:0')]
Total Average PSNR: 24.02
Number of samples: 1
CPU times: user 657 ms, sys: 361 ms, total: 1.02 s
Wall time: 1min 24s


In [43]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i in_rd_rdm_4_tt

INFO - main.py - 2023-04-07 22:51:21,130 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 76%|██████████████████████████████▌         | 924/1210 [00:49<00:19, 14.34it/s]


PSNR: 26.61: 100%|████████████████████████████████| 1/1 [01:03<00:00, 63.36s/it]
[tensor(26.6113, device='cuda:0')]
Total Average PSNR: 26.61
Number of samples: 1
CPU times: user 602 ms, sys: 354 ms, total: 956 ms
Wall time: 1min 23s


In [44]:
%%time
!python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i in_rd_rdm_5_tt

INFO - main.py - 2023-04-07 22:54:34,832 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 76%|██████████████████████████████▌         | 923/1210 [00:50<00:19, 14.46it/s]


PSNR: 26.91: 100%|████████████████████████████████| 1/1 [01:05<00:00, 65.19s/it]
[tensor(26.9115, device='cuda:0')]
Total Average PSNR: 26.91
Number of samples: 1
CPU times: user 659 ms, sys: 447 ms, total: 1.11 s
Wall time: 1min 25s


### Conditional

In [13]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_0_tt

INFO - main.py - 2023-04-22 13:34:01,702 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 51%|████████████████████▌                   | 622/1210 [00:55<01:06,  8.86it/s]


PSNR: 33.34: 100%|███████████████████████████████| 1/1 [01:40<00:00, 100.01s/it]
[tensor(33.3415, device='cuda:0')]
Total Average PSNR: 33.34
Number of samples: 1
CPU times: user 989 ms, sys: 367 ms, total: 1.36 s
Wall time: 2min


In [14]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_1_tt

INFO - main.py - 2023-04-22 13:36:24,704 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 52%|████████████████████▋                   | 626/1210 [00:57<01:07,  8.64it/s]


PSNR: 26.80: 100%|███████████████████████████████| 1/1 [01:42<00:00, 102.50s/it]
[tensor(26.8048, device='cuda:0')]
Total Average PSNR: 26.80
Number of samples: 1
CPU times: user 1.09 s, sys: 424 ms, total: 1.52 s
Wall time: 2min 4s


In [15]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_2_tt

INFO - main.py - 2023-04-22 13:39:03,316 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 52%|████████████████████▊                   | 628/1210 [00:55<01:13,  7.94it/s]


PSNR: 27.40: 100%|████████████████████████████████| 1/1 [01:39<00:00, 99.61s/it]
[tensor(27.4010, device='cuda:0')]
Total Average PSNR: 27.40
Number of samples: 1
CPU times: user 896 ms, sys: 362 ms, total: 1.26 s
Wall time: 1min 59s


In [16]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_3_tt

INFO - main.py - 2023-04-22 13:41:39,786 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 52%|████████████████████▊                   | 628/1210 [00:57<01:07,  8.65it/s]


PSNR: 24.08: 100%|███████████████████████████████| 1/1 [01:40<00:00, 100.06s/it]
[tensor(24.0816, device='cuda:0')]
Total Average PSNR: 24.08
Number of samples: 1
CPU times: user 857 ms, sys: 477 ms, total: 1.33 s
Wall time: 2min 1s


In [17]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_4_tt

INFO - main.py - 2023-04-22 13:45:48,945 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 52%|████████████████████▋                   | 624/1210 [00:55<01:06,  8.79it/s]


PSNR: 26.58: 100%|███████████████████████████████| 1/1 [01:40<00:00, 100.11s/it]
[tensor(26.5777, device='cuda:0')]
Total Average PSNR: 26.58
Number of samples: 1
CPU times: user 826 ms, sys: 625 ms, total: 1.45 s
Wall time: 1min 58s


In [18]:
%%time
!python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i cond_in_rd_rdm_5_tt

INFO - main.py - 2023-04-22 13:48:35,956 - Using device: cuda
Run SVD-based DDNM. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 52%|████████████████████▋                   | 627/1210 [00:56<01:08,  8.56it/s]


PSNR: 27.02: 100%|████████████████████████████████| 1/1 [01:39<00:00, 99.80s/it]
[tensor(27.0177, device='cuda:0')]
Total Average PSNR: 27.02
Number of samples: 1
CPU times: user 1.01 s, sys: 462 ms, total: 1.47 s
Wall time: 2min


# ALL TEST A

In [11]:
cd /workspace/DDNM/exp/datasets/imagenet/imagenet/

/workspace/DDNM/exp/datasets/imagenet/imagenet


In [12]:
rm -r .ipynb_checkpoints

In [13]:
cd /workspace/DDNM/

/workspace/DDNM


In [3]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
        
    #masking
    !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}
    

    temp = "FIX_simplified_"
    !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_old" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

    
    
    
    


Processing image: .ipynb_checkpoints
Traceback (most recent call last):
  File "/workspace/DDNM/exp/inp_masks_raindrop/get_mask.py", line 17, in <module>
    print(mask.shape)
AttributeError: 'NoneType' object has no attribute 'shape'
INFO - main.py - 2023-05-15 14:36:14,224 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:02<?, ?it/s]
ERROR - main.py - 2023-05-15 14:36:27,949 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 466, in simplified_ddnm_plus
    for x_orig, classes


PSNR: 38.87: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.95s/it]
[tensor(38.8675, device='cuda:0')]
Total Average PSNR: 38.87
Number of samples: 1
Processing image: 11_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:37:47,075 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.35: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.99s/it]
[tensor(27.3472, device='cuda:0')]
Total Average PSNR: 27.35
Number of samples: 1
Processing image: 12_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:38:21,209 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, trav

PSNR: 34.35: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.55s/it]
[tensor(34.3513, device='cuda:0')]
Total Average PSNR: 34.35
Number of samples: 1
Processing image: 14_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:39:33,469 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.91: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.98s/it]
[tensor(24.9137, device='cuda:0')]
Total Average PSNR: 24.91
Number of samples: 1
Processing image: 15_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:40:08,641 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, trave

PSNR: 27.43: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.80s/it]
[tensor(27.4348, device='cuda:0')]
Total Average PSNR: 27.43
Number of samples: 1
Processing image: 17_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:41:16,837 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.67: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.22s/it]
[tensor(27.6681, device='cuda:0')]
Total Average PSNR: 27.67
Number of samples: 1
Processing image: 18_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:41:50,902 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, trave

PSNR: 25.79: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.53s/it]
[tensor(25.7878, device='cuda:0')]
Total Average PSNR: 25.79
Number of samples: 1
Processing image: 1_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:43:01,027 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.63: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.16s/it]
[tensor(27.6339, device='cuda:0')]
Total Average PSNR: 27.63
Number of samples: 1
Processing image: 20_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 14:43:37,682 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel

...

Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.06: 100%|████████████████████████████████| 1/1 [00:20<00:00, 20.26s/it]
[tensor(27.0644, device='cuda:0')]
Total Average PSNR: 27.06
Number of samples: 1
Processing image: 51_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 15:04:17,344 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256

PSNR: 27.49: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.34s/it]
[tensor(27.4921, device='cuda:0')]
Total Average PSNR: 27.49
Number of samples: 1
Processing image: 54_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 15:06:11,078 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.24: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.56s/it]
[tensor(26.2396, device='cuda:0')]
Total Average PSNR: 26.24
Number of samples: 1
Processing image: 55_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 15:06:48,832 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, trave

PSNR: 32.52: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.68s/it]
[tensor(32.5223, device='cuda:0')]
Total Average PSNR: 32.52
Number of samples: 1
Processing image: 57_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 15:08:09,717 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 32.29: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.10s/it]
[tensor(32.2899, device='cuda:0')]
Total Average PSNR: 32.29
Number of samples: 1
Processing image: 5_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 15:08:43,175 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel

PSNR: 30.73: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.76s/it]
[tensor(30.7261, device='cuda:0')]
Total Average PSNR: 30.73
Number of samples: 1
Processing image: 7_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 15:09:52,604 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 29.48: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.22s/it]
[tensor(29.4835, device='cuda:0')]
Total Average PSNR: 29.48
Number of samples: 1
Processing image: 8_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-15 15:10:24,837 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_

PSNR: 27.00: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.76s/it]
[tensor(27.0011, device='cuda:0')]
Total Average PSNR: 27.00
Number of samples: 1


In [5]:
%time 

import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
        
    #masking
    !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}
    

    temp = "FIX_SVD_"
    !python main.py --ni --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

CPU times: user 2 µs, sys: 6 µs, total: 8 µs
Wall time: 13.4 µs
Processing image: 0_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:17:11,435 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.43: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.91s/it]
[tensor(33.4319, device='cuda:0')]
Total Average PSNR: 33.43
Number of samples: 1
Processing image: 10_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:17:54,223 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 38.34: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.83s/it]
[tensor(38.3366, device='cuda:0')]
Total Average PSNR: 38.34
Number of samples: 1

PSNR: 23.89: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.21s/it]
[tensor(23.8937, device='cuda:0')]
Total Average PSNR: 23.89
Number of samples: 1
Processing image: 13_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:20:12,033 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.25: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.91s/it]
[tensor(33.2549, device='cuda:0')]
Total Average PSNR: 33.25
Number of samples: 1


Processing image: 14_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:20:58,609 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 24.31: 100%|████████████████████████████████| 1/1 [00:22<00:00, 22.17s/it]
[tensor(24.3068, device='cuda:0')]
Total Average PSNR: 24.31
Number of samples: 1
Processing image: 15_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:21:49,699 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 28.23: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.08s/it]
[tensor(28.2286, device='cuda:0')]
Total Average PSNR: 28.23
Number of samples: 1
Processing image: 16_rain.png
(256, 256, 3)
(256, 256)
INFO - 

PSNR: 26.31: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.41s/it]
[tensor(26.3080, device='cuda:0')]
Total Average PSNR: 26.31
Number of samples: 1
Processing image: 18_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:24:09,124 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 22.92: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.46s/it]
[tensor(22.9226, device='cuda:0')]
Total Average PSNR: 22.92
Number of samples: 1
Processing image: 19_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:24:55,734 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 25.54: 100%|████████████████████████████████| 1/1 [00:18

PSNR: 26.09: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.41s/it]
[tensor(26.0883, device='cuda:0')]
Total Average PSNR: 26.09
Number of samples: 1
Processing image: 20_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:26:28,748 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 29.30: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.71s/it]
[tensor(29.3042, device='cuda:0')]
Total Average PSNR: 29.30
Number of samples: 1
Processing image: 21_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:27:12,893 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 25.14: 100%|████████████████████████████████| 1/1 [00:18

...

PSNR: 29.41: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.68s/it]
[tensor(29.4087, device='cuda:0')]
Total Average PSNR: 29.41
Number of samples: 1
Processing image: 50_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:51:02,313 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 26.61: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.53s/it]
[tensor(26.6105, device='cuda:0')]
Total Average PSNR: 26.61
Number of samples: 1
Processing image: 51_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:51:43,112 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 26.37: 100%|████████████████████████████████| 1/1 [00:16

PSNR: 26.44: 100%|████████████████████████████████| 1/1 [00:16<00:00, 17.00s/it]
[tensor(26.4415, device='cuda:0')]
Total Average PSNR: 26.44
Number of samples: 1
Processing image: 54_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:53:57,825 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 26.11: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.12s/it]
[tensor(26.1114, device='cuda:0')]
Total Average PSNR: 26.11
Number of samples: 1
Processing image: 55_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:54:39,841 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 23.23: 100%|████████████████████████████████| 1/1 [00:17

PSNR: 31.26: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.83s/it]
[tensor(31.2646, device='cuda:0')]
Total Average PSNR: 31.26
Number of samples: 1
Processing image: 57_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:56:09,505 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 31.91: 100%|████████████████████████████████| 1/1 [00:15<00:00, 15.38s/it]
[tensor(31.9137, device='cuda:0')]
Total Average PSNR: 31.91
Number of samples: 1
Processing image: 5_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:56:49,531 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 35.68: 100%|████████████████████████████████| 1/1 [00:19<

PSNR: 30.44: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.38s/it]
[tensor(30.4422, device='cuda:0')]
Total Average PSNR: 30.44
Number of samples: 1
Processing image: 7_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:58:21,869 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 28.51: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.76s/it]
[tensor(28.5069, device='cuda:0')]
Total Average PSNR: 28.51
Number of samples: 1
Processing image: 8_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 05:59:02,059 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 24.28: 100%|████████████████████████████████| 1/1 [00:19<0

PSNR: 26.79: 100%|████████████████████████████████| 1/1 [00:14<00:00, 14.91s/it]
[tensor(26.7927, device='cuda:0')]
Total Average PSNR: 26.79
Number of samples: 1


In [8]:
print(1)

1


In [6]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
        
    #masking
    !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}
    

    temp = "FIX_CONDITIONAL_SVD"
    !python main.py --ni --config imagenet_256_cc.yml --path_y raindrop --eta 0.85 --deg "inpainting" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

Processing image: 0_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:10:35,307 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.76: 100%|████████████████████████████████| 1/1 [00:24<00:00, 24.74s/it]
[tensor(33.7641, device='cuda:0')]
Total Average PSNR: 33.76
Number of samples: 1
Processing image: 10_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:11:26,495 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 80%|█████████████████████████████████▌        | 80/100 [00:17<00:02,  8.71it/s]


PSNR: 38.33: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.54s/it]
[tensor(38.3253, device='cuda:0')]
Total Average PSNR: 38.33
Number of samples: 1
Processing image: 11_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:12:20,432 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 26.27: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.58s/it]
[tensor(26.2741, device='cuda:0')]
Total Average PSNR: 26.27
Number of samples: 1
Processing image: 12_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:13:12,294 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 58%|████████████████████████▎                 | 58/100 [00:17

PSNR: 23.98: 100%|████████████████████████████████| 1/1 [00:25<00:00, 25.48s/it]
[tensor(23.9812, device='cuda:0')]
Total Average PSNR: 23.98
Number of samples: 1
Processing image: 13_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:14:05,963 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 33.46: 100%|████████████████████████████████| 1/1 [00:26<00:00, 26.08s/it]
[tensor(33.4553, device='cuda:0')]
Total Average PSNR: 33.46
Number of samples: 1
Processing image: 14_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:15:01,077 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 36%|███████████████                           | 36/100 [00:14

PSNR: 24.55: 100%|████████████████████████████████| 1/1 [00:25<00:00, 25.52s/it]
[tensor(24.5479, device='cuda:0')]
Total Average PSNR: 24.55
Number of samples: 1
Processing image: 15_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:15:55,569 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 28.56: 100%|████████████████████████████████| 1/1 [00:25<00:00, 25.99s/it]
[tensor(28.5580, device='cuda:0')]
Total Average PSNR: 28.56
Number of samples: 1
Processing image: 16_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:16:49,468 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 14%|█████▉                                    | 14/100 [00:13

PSNR: 27.38: 100%|████████████████████████████████| 1/1 [00:27<00:00, 27.80s/it]
[tensor(27.3841, device='cuda:0')]
Total Average PSNR: 27.38
Number of samples: 1
Processing image: 17_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:17:48,692 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
100%|█████████████████████████████████████████| 100/100 [00:25<00:00,  3.92it/s]


...

PSNR: 17.85: 100%|████████████████████████████████| 1/1 [00:28<00:00, 28.00s/it]
[tensor(17.8457, device='cuda:0')]
Total Average PSNR: 17.85
Number of samples: 1
Processing image: 40_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:41:17,808 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 28.60: 100%|████████████████████████████████| 1/1 [00:25<00:00, 25.48s/it]
[tensor(28.5988, device='cuda:0')]
Total Average PSNR: 28.60
Number of samples: 1
Processing image: 41_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:42:10,884 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
  2%|▊                                          | 2/100 [00:10

100%|█████████████████████████████████████████| 100/100 [00:22<00:00,  4.43it/s]


PSNR: 34.46: 100%|████████████████████████████████| 1/1 [00:25<00:00, 25.68s/it]
[tensor(34.4620, device='cuda:0')]
Total Average PSNR: 34.46
Number of samples: 1
Processing image: 42_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:43:05,244 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
PSNR: 24.62: 100%|████████████████████████████████| 1/1 [00:28<00:00, 28.06s/it]
[tensor(24.6189, device='cuda:0')]
Total Average PSNR: 24.62
Number of samples: 1
Processing image: 43_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:43:59,931 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
 78%|████████████████████████████████▊         | 78/100 [00:17

PSNR: 29.40: 100%|████████████████████████████████| 1/1 [00:23<00:00, 23.28s/it]
[tensor(29.3954, device='cuda:0')]
Total Average PSNR: 29.40
Number of samples: 1
Processing image: 44_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 06:44:50,908 - Using device: cuda
Run SVD-based DDNM. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: inpainting.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
Start from 0
  3%|█▎                                         | 3/100 [00:10<03:56,  2.44s/it]

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [1]:
# Set the iopub_msg_rate_limit value
%config NotebookApp.iopub_msg_rate_limit = 4000.0

In [2]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
        
    #masking
    !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}
    

    temp = "FIX_DG"
    !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 5.01 µs
Processing image: 0_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 07:52:50,914 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.13: 100%|████████████████████████████████| 1/1 [00:21<00:00, 21.87s/it]
[tensor(35.1322, device='cuda:0')]
Total Average PSNR: 35.13
Number of samples: 1
Processing image: 10_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 07:53:36,353 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt

  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 23.78: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.68s/it]
[tensor(23.7816, device='cuda:0')]
Total Average PSNR: 23.78
Number of samples: 1
Processing image: 13_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 07:56:42,102 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 34.19: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.79s/it]
[tensor(34.1910, device='cuda:0')]
Total Average PSNR: 34.19
Number of samples: 1
Processing image: 14_rain.png
(256, 256, 3)
(256, 2

PSNR: 29.81: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.02s/it]
[tensor(29.8069, device='cuda:0')]
Total Average PSNR: 29.81
Number of samples: 1
Processing image: 16_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 07:58:40,365 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.38: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.61s/it]
[tensor(27.3846, device='cuda:0')]
Total Average PSNR: 27.38
Number of samples: 1
Processing image: 17_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 07:59:19,409 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. trav

PSNR: 22.74: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.21s/it]
[tensor(22.7384, device='cuda:0')]
Total Average PSNR: 22.74
Number of samples: 1
Processing image: 19_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:00:45,202 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 25.72: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.72s/it]
[tensor(25.7168, device='cuda:0')]
Total Average PSNR: 25.72
Number of samples: 1
Processing image: 1_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:01:23,917 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. trave

PSNR: 30.55: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.71s/it]
[tensor(30.5493, device='cuda:0')]
Total Average PSNR: 30.55
Number of samples: 1
Processing image: 21_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:02:56,409 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 25.38: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.09s/it]
[tensor(25.3794, device='cuda:0')]
Total Average PSNR: 25.38
Number of samples: 1
Processing image: 22_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:03:34,006 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. trav

...

PSNR: 30.37: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.09s/it]
[tensor(30.3747, device='cuda:0')]
Total Average PSNR: 30.37
Number of samples: 1
Processing image: 50_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:27:18,532 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.96: 100%|████████████████████████████████| 1/1 [00:20<00:00, 20.02s/it]
[tensor(26.9574, device='cuda:0')]
Total Average PSNR: 26.96
Number of samples: 1
Processing image: 51_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:28:04,014 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. trav

PSNR: 25.07: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.99s/it]
[tensor(25.0707, device='cuda:0')]
Total Average PSNR: 25.07
Number of samples: 1
Processing image: 53_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:30:02,890 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.36: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.57s/it]
[tensor(27.3596, device='cuda:0')]
Total Average PSNR: 27.36
Number of samples: 1
Processing image: 54_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:30:44,880 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. trav

PSNR: 23.46: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.53s/it]
[tensor(23.4624, device='cuda:0')]
Total Average PSNR: 23.46
Number of samples: 1
Processing image: 56_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:32:09,954 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 32.29: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.29s/it]
[tensor(32.2857, device='cuda:0')]
Total Average PSNR: 32.29
Number of samples: 1
Processing image: 57_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:32:50,153 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. trav

PSNR: 35.66: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.99s/it]
[tensor(35.6613, device='cuda:0')]
Total Average PSNR: 35.66
Number of samples: 1
Processing image: 6_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:34:09,460 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 30.53: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.88s/it]
[tensor(30.5259, device='cuda:0')]
Total Average PSNR: 30.53
Number of samples: 1
Processing image: 7_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 08:34:57,635 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel

PSNR: 26.96: 100%|████████████████████████████████| 1/1 [00:21<00:00, 21.55s/it]
[tensor(26.9639, device='cuda:0')]
Total Average PSNR: 26.96
Number of samples: 1


In [3]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
        
    #masking
    !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}
    

    temp = "FIX_DU"
    !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_du" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

CPU times: user 1 µs, sys: 1 µs, total: 2 µs
Wall time: 3.58 µs
Processing image: 0_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:46:10,491 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.06: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.24s/it]
[tensor(35.0576, device='cuda:0')]
Total Average PSNR: 35.06
Number of samples: 1
Processing image: 10_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:46:50,970 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_v

PSNR: 23.76: 100%|████████████████████████████████| 1/1 [00:19<00:00, 20.00s/it]
[tensor(23.7623, device='cuda:0')]
Total Average PSNR: 23.76
Number of samples: 1
Processing image: 13_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:48:46,746 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 34.09: 100%|████████████████████████████████| 1/1 [00:22<00:00, 22.46s/it]
[tensor(34.0912, device='cuda:0')]
Total Average PSNR: 34.09
Number of samples: 1
Processing image: 14_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:49:29,608 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 24.82: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.68s/it]
[tensor(24.8195, device='cuda:0')]
Total Average PSNR: 24.82
Number of samples: 1
Processing image: 15_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:50:08,108 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 29.56: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.81s/it]
[tensor(29.5625, device='cuda:0')]
Total Average PSNR: 29.56
Number of samples: 1
Processing image: 16_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:50:46,343 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 27.53: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.15s/it]
[tensor(27.5281, device='cuda:0')]
Total Average PSNR: 27.53
Number of samples: 1
Processing image: 18_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:52:04,788 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 22.72: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.69s/it]
[tensor(22.7198, device='cuda:0')]
Total Average PSNR: 22.72
Number of samples: 1
Processing image: 19_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:52:41,364 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 27.45: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.83s/it]
[tensor(27.4503, device='cuda:0')]
Total Average PSNR: 27.45
Number of samples: 1
Processing image: 20_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:53:58,205 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 30.17: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.61s/it]
[tensor(30.1701, device='cuda:0')]
Total Average PSNR: 30.17
Number of samples: 1
Processing image: 21_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 09:54:37,114 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

...

PSNR: 26.90: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.22s/it]
[tensor(26.9005, device='cuda:0')]
Total Average PSNR: 26.90
Number of samples: 1
Processing image: 51_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:16:32,677 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.64: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.35s/it]
[tensor(26.6422, device='cuda:0')]
Total Average PSNR: 26.64
Number of samples: 1
Processing image: 52_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:17:13,579 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 27.25: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.19s/it]
[tensor(27.2512, device='cuda:0')]
Total Average PSNR: 27.25
Number of samples: 1
Processing image: 54_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:18:31,168 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.15: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.88s/it]
[tensor(26.1531, device='cuda:0')]
Total Average PSNR: 26.15
Number of samples: 1
Processing image: 55_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:19:11,275 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 32.10: 100%|████████████████████████████████| 1/1 [00:20<00:00, 20.08s/it]
[tensor(32.1027, device='cuda:0')]
Total Average PSNR: 32.10
Number of samples: 1
Processing image: 57_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:20:30,542 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 32.11: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.75s/it]
[tensor(32.1078, device='cuda:0')]
Total Average PSNR: 32.11
Number of samples: 1
Processing image: 5_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:21:08,011 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps.

Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.64: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.26s/it]
[tensor(35.6372, device='cuda:0')]
Total Average PSNR: 35.64
Number of samples: 1
Processing image: 6_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:21:44,695 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 30.45: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.09s/it]
[tensor(30.4508, device='cuda:0')]
Total Average PSNR: 30.45
Number of samples: 1
Processing image: 7_rain.png
(256

PSNR: 24.11: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.01s/it]
[tensor(24.1116, device='cuda:0')]
Total Average PSNR: 24.11
Number of samples: 1
Processing image: 9_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:23:29,786 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_du.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_du
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.89: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.88s/it]
[tensor(26.8923, device='cuda:0')]
Total Average PSNR: 26.89
Number of samples: 1


In [4]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    print ('Processing image: %s'%(input_list[i]))
    #imagenet txt
    file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

    # Step 2: Open the file in write mode and truncate its content
    with open(file_path, 'w') as file:
        file.truncate(0)

        # Step 3: Write to the file
        file.write(input_list[i])
        file.write(' 0')
        
    #masking
    !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}
    

    temp = "FIX_DA"
    !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 4.77 µs
Processing image: 0_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:38:02,549 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 35.05: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.31s/it]
[tensor(35.0526, device='cuda:0')]
Total Average PSNR: 35.05
Number of samples: 1
Processing image: 10_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:38:37,574 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_v

PSNR: 23.78: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.60s/it]
[tensor(23.7776, device='cuda:0')]
Total Average PSNR: 23.78
Number of samples: 1
Processing image: 13_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:40:35,409 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 34.16: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.10s/it]
[tensor(34.1583, device='cuda:0')]
Total Average PSNR: 34.16
Number of samples: 1
Processing image: 14_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:41:13,204 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 29.67: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.22s/it]
[tensor(29.6698, device='cuda:0')]
Total Average PSNR: 29.67
Number of samples: 1
Processing image: 16_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:42:24,598 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 27.36: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.63s/it]
[tensor(27.3606, device='cuda:0')]
Total Average PSNR: 27.36
Number of samples: 1
Processing image: 17_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:43:00,972 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 22.72: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.36s/it]
[tensor(22.7190, device='cuda:0')]
Total Average PSNR: 22.72
Number of samples: 1
Processing image: 19_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:44:12,149 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 25.72: 100%|████████████████████████████████| 1/1 [00:16<00:00, 16.57s/it]
[tensor(25.7181, device='cuda:0')]
Total Average PSNR: 25.72
Number of samples: 1
Processing image: 1_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:44:45,363 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps.

PSNR: 30.45: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.20s/it]
[tensor(30.4524, device='cuda:0')]
Total Average PSNR: 30.45
Number of samples: 1
Processing image: 21_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:45:57,154 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 25.37: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.86s/it]
[tensor(25.3748, device='cuda:0')]
Total Average PSNR: 25.37
Number of samples: 1
Processing image: 22_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 10:46:37,284 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

...

  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 30.22: 100%|████████████████████████████████| 1/1 [00:21<00:00, 21.72s/it]
[tensor(30.2206, device='cuda:0')]
Total Average PSNR: 30.22
Number of samples: 1
Processing image: 50_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 11:09:01,362 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 26.88: 100%|████████████████████████████████| 1/1 [00:22<00:00, 22.36s/it]
[tensor(26.8787, device='cuda:0')]
Total Average PSNR: 26.88
Number of samples: 1
Processing image: 51_rain.png
(256, 256, 3)
(

PSNR: 26.65: 100%|████████████████████████████████| 1/1 [00:20<00:00, 20.68s/it]
[tensor(26.6502, device='cuda:0')]
Total Average PSNR: 26.65
Number of samples: 1
Processing image: 52_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 11:10:26,785 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:01<?, ?it/s]
ERROR - main.py - 2023-05-16 11:10:41,386 - Traceback (most recent call last):
  File "/opt/conda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 990, in _try_get_data
    data = self._data_queue.get(timeout=timeout)
  File "/opt/conda/lib/python3.8/multiprocessing/queues.py", line 107, in get
    if not self._poll(timeout):
  File "/opt/conda/lib/python3

Processing image: 54_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 11:11:08,002 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:03<?, ?it/s]
ERROR - main.py - 2023-05-16 11:11:25,186 - Traceback (most recent call last):
  File "/opt/conda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 990, in _try_get_data
    data = self._data_queue.get(timeout=timeout)
  File "/opt/conda/lib/python3.8/multiprocessing/queues.py", line 107, in get
    if not self._poll(timeout):
  File "/opt/conda/lib/python3.8/multiprocessing/connection.py", line 257, in poll
    return self._poll(timeout)
  File "/opt/conda/lib/python3.8/multiprocessing/connection.py", line 424, in _

Processing image: 57_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 11:12:18,753 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:02<?, ?it/s]
ERROR - main.py - 2023-05-16 11:12:34,981 - Traceback (most recent call last):
  File "/opt/conda/lib/python3.8/site-packages/torch/utils/data/dataloader.py", line 990, in _try_get_data
    data = self._data_queue.get(timeout=timeout)
  File "/opt/conda/lib/python3.8/multiprocessing/queues.py", line 107, in get
    if not self._poll(timeout):
  File "/opt/conda/lib/python3.8/multiprocessing/connection.py", line 257, in poll
    return self._poll(timeout)
  File "/opt/conda/lib/python3.8/multiprocessing/connection.py", line 424, in _

Processing image: 7_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 11:13:21,196 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]
ERROR - main.py - 2023-05-16 11:13:35,512 - Traceback (most recent call last):
  File "main.py", line 166, in main
    runner.sample(args.simplified)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 284, in sample
    self.simplified_ddnm_plus(model, cls_fn)
  File "/workspace/DDNM/guided_diffusion/diffusion.py", line 466, in simplified_ddnm_plus
    for x_orig, classes in pbar:
  File "/opt/conda/lib/python3.8/site-packages/tqdm/std.py", line 1180, in __iter__
    for obj in iterable:
  File "/opt/conda/lib/python3.8/sit

In [10]:
!export CUDA_LAUNCH_BLOCKING=1

In [1]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] in ['52_rain.png',
 '53_rain.png',
 '54_rain.png',
 '55_rain.png',
 '56_rain.png',
 '57_rain.png',
 '5_rain.png',
 '6_rain.png',
 '7_rain.png',
 '8_rain.png',
 '9_rain.png']):
        print ('Processing image: %s'%(input_list[i]))
        #imagenet txt
        file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

        # Step 2: Open the file in write mode and truncate its content
        with open(file_path, 'w') as file:
            file.truncate(0)

            # Step 3: Write to the file
            file.write(input_list[i])
            file.write(' 0')

        #masking
        !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}


        temp = "FIX_DA"
        !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_da" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}

CPU times: user 1e+03 ns, sys: 1 µs, total: 2 µs
Wall time: 3.34 µs
Processing image: 52_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:51:34,798 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 25.04: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.33s/it]
[tensor(25.0428, device='cuda:0')]
Total Average PSNR: 25.04
Number of samples: 1
Processing image: 53_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:52:16,228 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/image

PSNR: 23.44: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.33s/it]
[tensor(23.4370, device='cuda:0')]
Total Average PSNR: 23.44
Number of samples: 1
Processing image: 56_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:54:35,571 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 32.23: 100%|████████████████████████████████| 1/1 [00:18<00:00, 18.41s/it]
[tensor(32.2348, device='cuda:0')]
Total Average PSNR: 32.23
Number of samples: 1
Processing image: 57_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:55:21,646 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps

PSNR: 35.67: 100%|████████████████████████████████| 1/1 [00:17<00:00, 17.51s/it]
[tensor(35.6721, device='cuda:0')]
Total Average PSNR: 35.67
Number of samples: 1
Processing image: 6_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:56:42,511 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 30.47: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.28s/it]
[tensor(30.4714, device='cuda:0')]
Total Average PSNR: 30.47
Number of samples: 1
Processing image: 7_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:57:23,124 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. 


PSNR: 29.28: 100%|████████████████████████████████| 1/1 [00:20<00:00, 20.37s/it]
[tensor(29.2804, device='cuda:0')]
Total Average PSNR: 29.28
Number of samples: 1
Processing image: 8_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:58:03,498 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps. travel_length = 1, travel_repeat = 1. Task: raindrop_mask_da.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_da
mask torch.Size([256, 256])
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

PSNR: 24.12: 100%|████████████████████████████████| 1/1 [00:19<00:00, 19.85s/it]
[tensor(24.1181, device='cuda:0')]
Total Average PSNR: 24.12
Number of samples: 1
Processing image: 9_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-16 12:58:43,941 - Using device: cuda
Run Simplified DDNM, without SVD. 100 sampling steps.

In [22]:

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
print(input_list)

['.ipynb_checkpoints', '0_rain.png', '10_rain.png', '11_rain.png', '12_rain.png', '13_rain.png', '14_rain.png', '15_rain.png', '16_rain.png', '17_rain.png', '18_rain.png', '19_rain.png', '1_rain.png', '20_rain.png', '21_rain.png', '22_rain.png', '23_rain.png', '24_rain.png', '25_rain.png', '26_rain.png', '27_rain.png', '28_rain.png', '29_rain.png', '2_rain.png', '30_rain.png', '31_rain.png', '32_rain.png', '33_rain.png', '34_rain.png', '35_rain.png', '36_rain.png', '37_rain.png', '38_rain.png', '39_rain.png', '3_rain.png', '40_rain.png', '41_rain.png', '42_rain.png', '43_rain.png', '44_rain.png', '45_rain.png', '46_rain.png', '47_rain.png', '48_rain.png', '49_rain.png', '4_rain.png', '50_rain.png', '51_rain.png', '52_rain.png', '53_rain.png', '54_rain.png', '55_rain.png', '56_rain.png', '57_rain.png', '5_rain.png', '6_rain.png', '7_rain.png', '8_rain.png', '9_rain.png']


In [23]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] in ['0_rain.png', '10_rain.png', '11_rain.png', '12_rain.png', '13_rain.png', '14_rain.png', '15_rain.png', '16_rain.png', '17_rain.png', '18_rain.png', '19_rain.png', '1_rain.png']):
        print ('Processing image: %s'%(input_list[i]))
        #imagenet txt
        file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

        # Step 2: Open the file in write mode and truncate its content
        with open(file_path, 'w') as file:
            file.truncate(0)

            # Step 3: Write to the file
            file.write(input_list[i])
            file.write(' 0')

        #masking
        !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}


        temp = "FIX_simplified_tt"
        !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_old" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}
    

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 4.77 µs
Processing image: 0_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:11:01,206 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 74%|█████████████████████████████▊          | 901/1210 [00:48<00:13, 23.06it/s]


PSNR: 36.13: 100%|████████████████████████████████| 1/1 [01:07<00:00, 67.08s/it]
[tensor(36.1331, device='cuda:0')]
Total Average PSNR: 36.13
Number of samples: 1
Processing image: 10_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:12:24,776 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 45%|██████████████████                      | 545/1210 [00:31<00:14, 44.95it/s]


PSNR: 39.63: 100%|████████████████████████████████| 1/1 [01:06<00:00, 66.20s/it]
[tensor(39.6302, device='cuda:0')]
Total Average PSNR: 39.63
Number of samples: 1
Processing image: 11_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:13:48,321 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 18%|███████▏                                | 216/1210 [00:15<01:05, 15.14it/s]


 96%|█████████████████████████████████████▍ | 1163/1210 [01:02<00:03, 14.84it/s]


PSNR: 28.63: 100%|████████████████████████████████| 1/1 [01:06<00:00, 66.85s/it]
[tensor(28.6288, device='cuda:0')]
Total Average PSNR: 28.63
Number of samples: 1
Processing image: 12_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:15:11,481 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 71%|████████████████████████████▏           | 854/1210 [00:49<00:11, 31.20it/s]


...

PSNR: 29.35: 100%|████████████████████████████████| 1/1 [01:08<00:00, 68.62s/it]
[tensor(29.3484, device='cuda:0')]
Total Average PSNR: 29.35
Number of samples: 1
Processing image: 18_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:23:56,902 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 60%|███████████████████████▉                | 723/1210 [00:40<00:37, 12.97it/s]


PSNR: 22.59: 100%|████████████████████████████████| 1/1 [01:08<00:00, 68.33s/it]
[tensor(22.5936, device='cuda:0')]
Total Average PSNR: 22.59
Number of samples: 1
Processing image: 19_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:25:22,912 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 30%|████████████▏                           | 369/1210 [00:23<00:54, 15.31it/s]


PSNR: 25.88: 100%|████████████████████████████████| 1/1 [01:10<00:00, 70.26s/it]
[tensor(25.8761, device='cuda:0')]
Total Average PSNR: 25.88
Number of samples: 1
Processing image: 1_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:26:50,278 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  5%|██                                       | 60/1210 [00:08<00:50, 22.72it/s]


 84%|████████████████████████████████▋      | 1016/1210 [00:56<00:12, 15.81it/s]


PSNR: 29.96: 100%|████████████████████████████████| 1/1 [01:08<00:00, 68.75s/it]
[tensor(29.9565, device='cuda:0')]
Total Average PSNR: 29.96
Number of samples: 1


In [24]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] in ['20_rain.png', '21_rain.png', '22_rain.png', '23_rain.png', '24_rain.png', '25_rain.png', '26_rain.png', '27_rain.png', '28_rain.png', '29_rain.png', '2_rain.png']):
        print ('Processing image: %s'%(input_list[i]))
        #imagenet txt
        file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

        # Step 2: Open the file in write mode and truncate its content
        with open(file_path, 'w') as file:
            file.truncate(0)

            # Step 3: Write to the file
            file.write(input_list[i])
            file.write(' 0')

        #masking
        !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}


        temp = "FIX_simplified_tt"
        !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_old" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}
    

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 5.01 µs
Processing image: 20_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:40:49,055 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 75%|█████████████████████████████▉          | 904/1210 [00:51<00:15, 19.91it/s]


PSNR: 31.19: 100%|████████████████████████████████| 1/1 [01:10<00:00, 70.29s/it]
[tensor(31.1886, device='cuda:0')]
Total Average PSNR: 31.19
Number of samples: 1
Processing image: 21_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:42:16,649 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 46%|██████████████████▍                     | 559/1210 [00:32<00:28, 22.77it/s]


PSNR: 25.58: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.78s/it]
[tensor(25.5835, device='cuda:0')]
Total Average PSNR: 25.58
Number of samples: 1
Processing image: 22_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:43:44,090 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 17%|██████▉                                 | 210/1210 [00:15<00:59, 16.80it/s]


 93%|████████████████████████████████████▎  | 1125/1210 [01:01<00:06, 12.54it/s]


PSNR: 29.00: 100%|████████████████████████████████| 1/1 [01:08<00:00, 68.12s/it]
[tensor(29.0037, device='cuda:0')]
Total Average PSNR: 29.00
Number of samples: 1
Processing image: 23_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:45:09,036 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 66%|██████████████████████████▍             | 801/1210 [00:44<00:17, 23.31it/s]


...

PSNR: 25.18: 100%|████████████████████████████████| 1/1 [01:07<00:00, 67.29s/it]
[tensor(25.1816, device='cuda:0')]
Total Average PSNR: 25.18
Number of samples: 1
Processing image: 28_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:52:19,766 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  2%|▉                                        | 28/1210 [00:07<01:45, 11.17it/s]


 82%|████████████████████████████████▋       | 990/1210 [00:55<00:04, 47.10it/s]


PSNR: 35.92: 100%|████████████████████████████████| 1/1 [01:10<00:00, 70.11s/it]
[tensor(35.9240, device='cuda:0')]
Total Average PSNR: 35.92
Number of samples: 1
Processing image: 29_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:53:48,684 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 55%|██████████████████████                  | 669/1210 [00:37<00:34, 15.84it/s]


PSNR: 30.52: 100%|████████████████████████████████| 1/1 [01:07<00:00, 67.33s/it]
[tensor(30.5209, device='cuda:0')]
Total Average PSNR: 30.52
Number of samples: 1
Processing image: 2_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 04:55:12,059 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 27%|██████████▊                             | 328/1210 [00:23<01:11, 12.39it/s]


PSNR: 27.57: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.24s/it]
[tensor(27.5739, device='cuda:0')]
Total Average PSNR: 27.57
Number of samples: 1


In [25]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] in ['30_rain.png', '31_rain.png', '32_rain.png', '33_rain.png', '34_rain.png', '35_rain.png', '36_rain.png', '37_rain.png', '38_rain.png', '39_rain.png', '3_rain.png']):
        print ('Processing image: %s'%(input_list[i]))
        #imagenet txt
        file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

        # Step 2: Open the file in write mode and truncate its content
        with open(file_path, 'w') as file:
            file.truncate(0)

            # Step 3: Write to the file
            file.write(input_list[i])
            file.write(' 0')

        #masking
        !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}


        temp = "FIX_simplified_tt"
        !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_old" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}
    

CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 4.29 µs
Processing image: 30_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:16:36,794 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 72%|████████████████████████████▋           | 866/1210 [00:48<00:18, 18.13it/s]


PSNR: 22.82: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.37s/it]
[tensor(22.8195, device='cuda:0')]
Total Average PSNR: 22.82
Number of samples: 1
Processing image: 31_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:18:03,541 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 43%|█████████████████▎                      | 522/1210 [00:31<00:51, 13.39it/s]


PSNR: 34.27: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.28s/it]
[tensor(34.2711, device='cuda:0')]
Total Average PSNR: 34.27
Number of samples: 1
Processing image: 32_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:19:30,224 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 18%|███████                                 | 214/1210 [00:16<01:04, 15.37it/s]


 96%|█████████████████████████████████████▍ | 1160/1210 [01:03<00:02, 23.09it/s]


PSNR: 28.87: 100%|████████████████████████████████| 1/1 [01:08<00:00, 68.57s/it]
[tensor(28.8745, device='cuda:0')]
Total Average PSNR: 28.87
Number of samples: 1
Processing image: 33_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:20:57,229 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 68%|███████████████████████████             | 820/1210 [00:47<00:28, 13.71it/s]


...

PSNR: 23.46: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.32s/it]
[tensor(23.4609, device='cuda:0')]
Total Average PSNR: 23.46
Number of samples: 1
Processing image: 38_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:28:15,763 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 18%|███████▏                                | 216/1210 [00:17<01:08, 14.48it/s]


PSNR: 28.37: 100%|████████████████████████████████| 1/1 [01:13<00:00, 73.73s/it]
[tensor(28.3698, device='cuda:0')]
Total Average PSNR: 28.37
Number of samples: 1
Processing image: 39_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:29:52,158 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 10%|███▉                                    | 119/1210 [00:11<01:16, 14.22it/s]


 88%|██████████████████████████████████▍    | 1068/1210 [00:59<00:08, 16.24it/s]


PSNR: 30.22: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.48s/it]
[tensor(30.2181, device='cuda:0')]
Total Average PSNR: 30.22
Number of samples: 1
Processing image: 3_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:31:20,983 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 66%|██████████████████████████▍             | 801/1210 [00:45<00:19, 21.27it/s]


PSNR: 18.14: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.68s/it]
[tensor(18.1439, device='cuda:0')]
Total Average PSNR: 18.14
Number of samples: 1


In [26]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] in ['40_rain.png', '41_rain.png', '42_rain.png', '43_rain.png', '44_rain.png', '45_rain.png', '46_rain.png', '47_rain.png', '48_rain.png', '49_rain.png', '4_rain.png']):
        print ('Processing image: %s'%(input_list[i]))
        #imagenet txt
        file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

        # Step 2: Open the file in write mode and truncate its content
        with open(file_path, 'w') as file:
            file.truncate(0)

            # Step 3: Write to the file
            file.write(input_list[i])
            file.write(' 0')

        #masking
        !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}


        temp = "FIX_simplified_tt"
        !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_old" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}
    

CPU times: user 2 µs, sys: 1e+03 ns, total: 3 µs
Wall time: 4.77 µs
Processing image: 40_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:47:47,228 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 74%|█████████████████████████████▍          | 891/1210 [00:49<00:07, 42.50it/s]


PSNR: 29.52: 100%|████████████████████████████████| 1/1 [01:10<00:00, 70.47s/it]
[tensor(29.5202, device='cuda:0')]
Total Average PSNR: 29.52
Number of samples: 1
Processing image: 41_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:49:16,205 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 43%|█████████████████▎                      | 523/1210 [00:31<00:54, 12.63it/s]


PSNR: 36.32: 100%|████████████████████████████████| 1/1 [01:08<00:00, 68.20s/it]
[tensor(36.3227, device='cuda:0')]
Total Average PSNR: 36.32
Number of samples: 1
Processing image: 42_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:50:44,282 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 17%|██████▊                                 | 207/1210 [00:15<00:57, 17.39it/s]


 95%|█████████████████████████████████████▏ | 1155/1210 [01:02<00:01, 30.44it/s]


PSNR: 24.69: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.53s/it]
[tensor(24.6869, device='cuda:0')]
Total Average PSNR: 24.69
Number of samples: 1
Processing image: 43_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:52:11,764 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 67%|██████████████████████████▋             | 809/1210 [00:46<00:22, 17.50it/s]


...

PSNR: 25.08: 100%|████████████████████████████████| 1/1 [01:07<00:00, 67.90s/it]
[tensor(25.0847, device='cuda:0')]
Total Average PSNR: 25.08
Number of samples: 1
Processing image: 48_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 05:59:37,235 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 49%|███████████████████▋                    | 595/1210 [00:34<00:21, 28.84it/s]


PSNR: 24.70: 100%|████████████████████████████████| 1/1 [01:09<00:00, 69.13s/it]
[tensor(24.7019, device='cuda:0')]
Total Average PSNR: 24.70
Number of samples: 1
Processing image: 49_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:01:04,202 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 18%|███████▎                                | 221/1210 [00:16<01:14, 13.26it/s]


 96%|█████████████████████████████████████▍ | 1160/1210 [01:02<00:02, 23.69it/s]


PSNR: 33.87: 100%|████████████████████████████████| 1/1 [01:07<00:00, 67.80s/it]
[tensor(33.8662, device='cuda:0')]
Total Average PSNR: 33.87
Number of samples: 1
Processing image: 4_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:02:29,049 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 74%|█████████████████████████████▋          | 898/1210 [00:54<00:13, 22.68it/s]


PSNR: 31.89: 100%|████████████████████████████████| 1/1 [01:15<00:00, 75.17s/it]
[tensor(31.8916, device='cuda:0')]
Total Average PSNR: 31.89
Number of samples: 1


In [27]:
%time
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] in ['50_rain.png', '51_rain.png', '52_rain.png', '53_rain.png', '54_rain.png', '55_rain.png', '56_rain.png', '57_rain.png', '5_rain.png', '6_rain.png', '7_rain.png', '8_rain.png', '9_rain.png']):
        print ('Processing image: %s'%(input_list[i]))
        #imagenet txt
        file_path = '/workspace/DDNM/exp/imagenet_val_1k.txt'

        # Step 2: Open the file in write mode and truncate its content
        with open(file_path, 'w') as file:
            file.truncate(0)

            # Step 3: Write to the file
            file.write(input_list[i])
            file.write(' 0')

        #masking
        !python /workspace/DDNM/exp/inp_masks_raindrop/get_mask.py --file {input_list[i]}


        temp = "FIX_simplified_tt"
        !python main.py --ni --simplified --config imagenet_256.yml --path_y raindrop --eta 0.85 --deg "raindrop_mask_old" --sigma_y 0.1 -i {temp+input_list[i].split(".")[0]}
    

CPU times: user 1e+03 ns, sys: 1 µs, total: 2 µs
Wall time: 3.58 µs
Processing image: 50_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:04:08,336 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 74%|█████████████████████████████▍          | 890/1210 [00:48<00:07, 42.08it/s]


PSNR: 27.54: 100%|████████████████████████████████| 1/1 [01:07<00:00, 67.81s/it]
[tensor(27.5401, device='cuda:0')]
Total Average PSNR: 27.54
Number of samples: 1
Processing image: 51_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:05:35,759 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 46%|██████████████████▍                     | 559/1210 [00:33<00:28, 22.77it/s]


PSNR: 26.70: 100%|████████████████████████████████| 1/1 [01:08<00:00, 68.18s/it]
[tensor(26.7003, device='cuda:0')]
Total Average PSNR: 26.70
Number of samples: 1
Processing image: 52_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:07:03,487 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 18%|███████▎                                | 221/1210 [00:20<01:21, 12.13it/s]


PSNR: 25.18: 100%|████████████████████████████████| 1/1 [01:19<00:00, 79.12s/it]
[tensor(25.1804, device='cuda:0')]
Total Average PSNR: 25.18
Number of samples: 1
Processing image: 53_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:08:47,634 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

  1%|▎                                         | 8/1210 [00:06<07:32,  2.65it/s]


 85%|█████████████████████████████████      | 1027/1210 [01:03<00:16, 11.31it/s]


...

PSNR: 31.30: 100%|████████████████████████████████| 1/1 [01:07<00:00, 67.03s/it]
[tensor(31.2989, device='cuda:0')]
Total Average PSNR: 31.30
Number of samples: 1
Processing image: 7_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:19:10,965 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 50%|████████████████████                    | 608/1210 [00:37<00:34, 17.64it/s]


PSNR: 30.38: 100%|████████████████████████████████| 1/1 [01:11<00:00, 71.32s/it]
[tensor(30.3780, device='cuda:0')]
Total Average PSNR: 30.38
Number of samples: 1
Processing image: 8_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:20:40,362 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 25%|█████████▊                              | 297/1210 [00:20<00:35, 26.01it/s]


100%|███████████████████████████████████████| 1210/1210 [01:06<00:00, 18.25it/s]


PSNR: 24.22: 100%|████████████████████████████████| 1/1 [01:10<00:00, 70.64s/it]
[tensor(24.2222, device='cuda:0')]
Total Average PSNR: 24.22
Number of samples: 1
Processing image: 9_rain.png
(256, 256, 3)
(256, 256)
INFO - main.py - 2023-05-18 06:22:09,061 - Using device: cuda
Run Simplified DDNM, without SVD. 250 sampling steps. travel_length = 20, travel_repeat = 3. Task: raindrop_mask_old.
building dataset from exp/imagenet_val_1k.txt
read meta done
Dataset has size 1
args.deg: raindrop_mask_old
Start from 0
  0%|                                                     | 0/1 [00:00<?, ?it/s]x_orig shape: torch.Size([1, 3, 256, 256])

 74%|█████████████████████████████▍          | 890/1210 [00:47<00:07, 42.56it/s]


PSNR: 26.94: 100%|████████████████████████████████| 1/1 [01:06<00:00, 66.33s/it]
[tensor(26.9419, device='cuda:0')]
Total Average PSNR: 26.94
Number of samples: 1


# COPY ALL TEST

In [ ]:
temp = "9_rain"
cp /workspace/DDNM/exp/image_samples/FIX_DA{temp}/-1_0.png /workspace/DDNM/exp/image_samples/FIX_DA/{temp}.png

In [2]:
import shutil

temp = "9_rain"
source_path = "/workspace/DDNM/exp/image_samples/FIX_DA" + temp + "/-1_0.png"
destination_path = "/workspace/DDNM/exp/image_samples/FIX_DA/" + temp + ".png"

shutil.copy(source_path, destination_path)

'/workspace/DDNM/exp/image_samples/FIX_DA/9_rain.png'

In [30]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_simplified_tt" + input_list[i].split(".")[0] + "/-1_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_simplified_tt/res/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [31]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_simplified_tt" + input_list[i].split(".")[0] + "/Apy/Apy_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_simplified_tt/apy/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [12]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_CONDITIONAL_SVD" + input_list[i].split(".")[0] + "/0_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_CONDITIONAL_SVD/res/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [14]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_CONDITIONAL_SVD" + input_list[i].split(".")[0] + "/Apy/Apy_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_CONDITIONAL_SVD/apy/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [11]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_simplified_" + input_list[i].split(".")[0] + "/-1_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_simplified/res/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [16]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_simplified_" + input_list[i].split(".")[0] + "/Apy/Apy_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_simplified/apy/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [10]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_SVD_" + input_list[i].split(".")[0] + "/0_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_SVD/res/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [17]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_SVD_" + input_list[i].split(".")[0] + "/Apy/Apy_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_SVD/apy/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [6]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_DG" + input_list[i].split(".")[0] + "/-1_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_DG/res/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [18]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_DG" + input_list[i].split(".")[0] + "/Apy/Apy_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_DG/apy/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [5]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_DU" + input_list[i].split(".")[0] + "/-1_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_DU/res/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [19]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_DU" + input_list[i].split(".")[0] + "/Apy/Apy_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_DU/apy/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [4]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_DA" + input_list[i].split(".")[0] + "/-1_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_DA/res/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im

In [20]:
import os

input_list = sorted(os.listdir("/workspace/DDNM/exp/datasets/imagenet/imagenet/"))
num = len(input_list)
for i in range(num):
    if(input_list[i] not in ['.ipynb_checkpoints']):
        print ('Processing image: %s'%(input_list[i]))
        source_path = "/workspace/DDNM/exp/image_samples/FIX_DA" + input_list[i].split(".")[0] + "/Apy/Apy_0.png"
        destination_path = "/workspace/DDNM/exp/image_samples/FIX_DA/apy/" + input_list[i].split(".")[0] + ".png"
        shutil.copy(source_path, destination_path)
    

Processing image: 0_rain.png
Processing image: 10_rain.png
Processing image: 11_rain.png
Processing image: 12_rain.png
Processing image: 13_rain.png
Processing image: 14_rain.png
Processing image: 15_rain.png
Processing image: 16_rain.png
Processing image: 17_rain.png
Processing image: 18_rain.png
Processing image: 19_rain.png
Processing image: 1_rain.png
Processing image: 20_rain.png
Processing image: 21_rain.png
Processing image: 22_rain.png
Processing image: 23_rain.png
Processing image: 24_rain.png
Processing image: 25_rain.png
Processing image: 26_rain.png
Processing image: 27_rain.png
Processing image: 28_rain.png
Processing image: 29_rain.png
Processing image: 2_rain.png
Processing image: 30_rain.png
Processing image: 31_rain.png
Processing image: 32_rain.png
Processing image: 33_rain.png
Processing image: 34_rain.png
Processing image: 35_rain.png
Processing image: 36_rain.png
Processing image: 37_rain.png
Processing image: 38_rain.png
Processing image: 39_rain.png
Processing im